In [1]:
# from openhealthdata import ClinicalTrialsGov

import pandas as pd
import plotly.express as px
pd.options.display.max_columns = None

def protocol_feature_query():
  print("loads selected features. Phase 2, 3, 4 Trials. Takes ~20 seconds to load")
  df = pd.read_parquet("https://storage.googleapis.com/data.openhealthdata.org/clinical_trials_gov/protocol_feature_cache.parquet")
  return df

protocol_feature = protocol_feature_query()
protocol_feature

loads selected features. Phase 2, 3, 4 Trials. Takes ~20 seconds to load


_trial_id                               _org_name _org_class  \
0       NCT04834349             M.D. Anderson Cancer Center      OTHER   
1       NCT04837924              General Hospital Sveti Duh      OTHER   
2       NCT04838444                    Valneva Austria GmbH   INDUSTRY   
3       NCT04831736                      NYU Langone Health      OTHER   
4       NCT04837820  Memorial Sloan Kettering Cancer Center      OTHER   
...             ...                                     ...        ...   
117240  NCT00554723                          CHIMES Society      OTHER   
117241  NCT00559845                       Hoffmann-La Roche   INDUSTRY   
117242  NCT00552136            Nova Scotia Health Authority      OTHER   
117243  NCT00556933                  University of Nebraska      OTHER   
117244  NCT00558311            Idorsia Pharmaceuticals Ltd.   INDUSTRY   

                                 _sponsor_name _sponsor_class  \
0                  M.D. Anderson Cancer Center          OTHER   
1                   General Hospital Sveti Duh          OTHER   
2                         Valneva Austria GmbH       INDUSTRY   
3                           NYU Langone Health          OTHER   
4       Memorial Sloan Kettering Cancer Center          OTHER   
...                                        ...            ...   
117240                          CHIMES Society          OTHER   
117241                       Hoffmann-La Roche       INDUSTRY   
117242                           Ross Leighton          OTHER   
117243                    R. Brian Stevens, MD          OTHER   
117244            Idorsia Pharmaceuticals Ltd.       INDUSTRY   

                                            _collaborator  \
0                                                    None   
1                                                    None   
2                                                    None   
3                                                    None   
4                                                    None   
...                                                   ...   
117240  [{'CollaboratorClass': 'OTHER_GOV', 'Collabora...   
117241                                               None   
117242  [{'CollaboratorClass': 'OTHER', 'CollaboratorN...   
117243  [{'CollaboratorClass': 'INDUSTRY', 'Collaborat...   
117244                                               None   

                                               _condition  \
0       [Recurrent Head and Neck Squamous Cell Carcino...   
1                                         [Hip Fractures]   
2                           [Chikungunya Virus Infection]   
3                                    [Postoperative Pain]   
4                                         [Breast Cancer]   
...                                                   ...   
117240                      [Cerebral Infarction, Stroke]   
117241                                    [Breast Cancer]   
117242                                  [Ankle Arthritis]   
117243                          [End-stage Renal Disease]   
117244               [Aneurysmal Subarachnoid Hemorrhage]   

                                                _location  \
0       [{'LocationCity': 'Houston', 'LocationContactL...   
1       [{'LocationCity': 'Zagreb', 'LocationContactLi...   
2       [{'LocationCity': 'Phoenix', 'LocationContactL...   
3       [{'LocationCity': 'New York', 'LocationContact...   
4       [{'LocationCity': 'Commack', 'LocationContactL...   
...                                                   ...   
117240  [{'LocationCity': 'Hong Kong', 'LocationContac...   
117241  [{'LocationCity': 'Napoli', 'LocationContactLi...   
117242  [{'LocationCity': 'Halifax', 'LocationContactL...   
117243  [{'LocationCity': 'Omaha', 'LocationContactLis...   
117244  [{'LocationCity': 'Phoenix', 'LocationContactL...   

                                             _eligibility  \
0       Inclusion Criteria:\n\nPatients with biopsy pr...   
1       Inclusion C

In [2]:
protocol_feature['_org_name'].value_counts()

Novartis                                    2306
GlaxoSmithKline                             1930
Pfizer                                      1553
National Cancer Institute (NCI)             1501
Sanofi                                      1484
                                            ... 
Igy Inc.                                       1
Entegrion, Inc.                                1
Shenzhen Zhongshan Urology Hospital            1
Centro en Insuficiencia Cardiaca, Mexico       1
CHIMES Society                                 1
Name: _org_name, Length: 11071, dtype: int64

In [3]:
protocol_feature = protocol_feature[protocol_feature['_start_yr'] > 1999]
protocol_feature = protocol_feature[protocol_feature['_start_yr'] < 2023]
px.box(
    protocol_feature,
    x="_start_yr",
    y="_arm_count",
    title=f"n={len(protocol_feature)} Studies",
    facet_col="_random",
)

In [4]:
def _get_us_locations(protocol_feature: pd.DataFrame, country: list = ["United States"]) -> pd.DataFrame:
    """
        1. Get locations of Phase 2, 3, 4 trials
        2. Adds the geocoordinates of the zip code where it takes place
    """
    df = protocol_feature
    df = df[df['_location_count_z'] < 3] # filter < 3 sigma 
    # df = df[df['_location_count'] > 0] 
    df = df.sort_values("_location_count")
    df = df[['_trial_id','_location','_phase','_location_count','_org_name']].reset_index(drop=True)
    dff = df.explode("_location").reset_index()

    location = pd.json_normalize(dff['_location']) #.reset_index()
    location = location.join(dff[['index','_trial_id','_location_count','_phase','_org_name']])
    location = location[location['LocationCountry'].isin(country)]
    location = location.drop(columns=['LocationContactList.LocationContact','LocationCountry','LocationContactList'])
    location = location.dropna(subset=["LocationStatus"]).reset_index(drop=True)

    def _geolocate_zip5(df):
        zip5_census = pd.read_feather("https://storage.googleapis.com/ph-cdn/us_census_zips_geo/adi_stats_zip5.feather")
        zip5_census = zip5_census.drop(columns=['count','adi_mean','min','max','std'])
        return df.merge(zip5_census, left_on="LocationZip", right_on="_zip5")

    location = _geolocate_zip5(location)
    
    return location

location = _get_us_locations(protocol_feature)
location

LocationCity                                   LocationFacility  \
0          Houston                         M D Anderson Cancer Center   
1          Houston                         M D Anderson Cancer Center   
2          Houston                         M D Anderson Cancer Center   
3          Houston                         M D Anderson Cancer Center   
4          Houston  The University of Texas Health Science Center ...   
...            ...                                                ...   
37251      Solvang                                      Sansum Clinic   
37252     Palm Bay                      Cancer Care Center of Brevard   
37253       Naples           Advanced Research for Health Improvement   
37254      Chicago                     Northwestern Memorial Hospital   
37255       Duluth                                      Research Site   

      LocationState          LocationStatus LocationZip   index    _trial_id  \
0             Texas              Recruiting       77030       0  NCT04834349   
1             Texas              Recruiting       77030      13  NCT04947254   
2             Texas              Recruiting       77030      24  NCT04940286   
3             Texas              Recruiting       77030      70  NCT04940299   
4             Texas              Recruiting       77030     361  NCT04570475   
...             ...                     ...         ...     ...          ...   
37251    California  Active, not recruiting       93463  100043  NCT03706365   
37252       Florida  Active, not recruiting       32909  100043  NCT03706365   
37253       Florida  Active, not recruiting       34109  100072  NCT03832946   
37254      Illinois              Recruiting       97232  100072  NCT03832946   
37255     Minnesota      Not yet recruiting       55812  100136  NCT05221840   

       _location_count   _phase  \
0                  1.0  Phase 2   
1                  1.0  Phase 2   
2                  1.0  Phase 2   
3                  1.0  Phase 2   
4                  1.0  Phase 3   
...                ...      ...   
37251            117.0  Phase 2   
37252            117.0  Phase 2   
37253            120.0  Phase 2   
37254            120.0  Phase 2   
37255            129.0  Phase 3   

                                               _org_name _state  _zip5  \
0                            M.D. Anderson Cancer Center     TX  77030   
1                            M.D. Anderson Cancer Center     TX  77030   
2                            M.D. Anderson Cancer Center     TX  77030   
3                            M.D. Anderson Cancer Center     TX  77030   
4      The University of Texas Health Science Center,...     TX  77030   
...                                                  ...    ...    ...   
37251                              Eli Lilly and Company     CA  93463   
37252                              Eli Lilly and Company     FL  32909   
37253                                 Galecto Biotech AB     FL  34109   
37254                                 Galecto Biotech AB     OR  97232   
37255                                        AstraZeneca     MN  55812   

       adi_median       _lat        _lng  _census_total  
0            10.0  29.705557  -95.401754          10258  
1            10.0  29.705557  -95.401754          10258  
2            10.0  29.705557  -95.401754          10258  
3            10.0  29.705557  -95.401754          10258  
4            10.0  29.705557  -95.401754          10258  
...           ...        ...         ...            ...  
37251         6.0  34.606422 -120.135431           7646  
37252        62.0  27.899533  -80.659568          30120  
37253        20.0  26.240842  -81.763823          23338  
37254        14.0  45.528929 -122.643927          11472  
37255        49.0  46.809362  -92.071786          10924  

[37256 rows x 16 columns]

In [5]:
px.set_mapbox_access_token("pk.eyJ1IjoicGFycXVhciIsImEiOiJja3lpcXMycGUxbmF5MnBzZXVzMHBzaXl4In0.jz0tx-HTJWym8jWPa8lqiA")

px.scatter_mapbox(
        location,
        lat="_lat",
        lon="_lng",
        title=f"Where do Clinical Trials take place? {len(location)} locations",
        color='LocationStatus',
        hover_data=['LocationFacility'],
        size_max=15,
        height=700,
        zoom=3,
    )